In [1]:
import polaris as po

competition = po.load_competition("asap-discovery/antiviral-ligand-poses-2025")

[2025-02-04 13:45:15] INFO     The version of Polaris that was used to create the artifact (0.11.0) ]8;id=973609;file:///home/hmacdope/mambaforge/envs/asap_v13/lib/python3.11/site-packages/polaris/_artifact.py\_artifact.py]8;;\:]8;id=449307;file:///home/hmacdope/mambaforge/envs/asap_v13/lib/python3.11/site-packages/polaris/_artifact.py#92\92]8;;\
                               is different from the currently installed version of Polaris                        
                               (0.11.6).                                                                           

                      WARNING  You're loading data from a remote location. If the dataset is small     ]8;id=743220;file:///home/hmacdope/mambaforge/envs/asap_v13/lib/python3.11/site-packages/polaris/dataset/_base.py\_base.py]8;;\:]8;id=699805;file:///home/hmacdope/mambaforge/envs/asap_v13/lib/python3.11/site-packages/polaris/dataset/_base.py#182\182]8;;\
                               enough, consider caching the dataset first using                                    
                               CompetitionSpecification.cache() for more performant data access.                   

In [2]:
competition.cache()


Output()

[13:45:17] Copying to destination                                                                      ]8;id=150703;file:///home/hmacdope/mambaforge/envs/asap_v13/lib/python3.11/site-packages/polaris/dataset/_base.py\_base.py]8;;\:]8;id=518091;file:///home/hmacdope/mambaforge/envs/asap_v13/lib/python3.11/site-packages/polaris/dataset/_base.py#381\381]8;;\
           /home/hmacdope/.cache/polaris/datasets/a8f8f2ee-a9c2-46ae-9693-b1f3f931e663/data.zarr                   

           For large Zarr archives, this may take a while.                                             ]8;id=982406;file:///home/hmacdope/mambaforge/envs/asap_v13/lib/python3.11/site-packages/polaris/dataset/_base.py\_base.py]8;;\:]8;id=115826;file:///home/hmacdope/mambaforge/envs/asap_v13/lib/python3.11/site-packages/polaris/dataset/_base.py#382\382]8;;\

[13:45:47]  Success: Copying Zarr keys                                                                ]8;id=893941;file:///home/hmacdope/mambaforge/envs/asap_v13/lib/python3.11/site-packages/polaris/utils/context.py\context.py]8;;\:]8;id=186515;file:///home/hmacdope/mambaforge/envs/asap_v13/lib/python3.11/site-packages/polaris/utils/context.py#53\53]8;;\

            Success: Copying Zarr archive                                                             ]8;id=645669;file:///home/hmacdope/mambaforge/envs/asap_v13/lib/python3.11/site-packages/polaris/utils/context.py\context.py]8;;\:]8;id=257161;file:///home/hmacdope/mambaforge/envs/asap_v13/lib/python3.11/site-packages/polaris/utils/context.py#53\53]8;;\

'/home/hmacdope/.cache/polaris/datasets/a8f8f2ee-a9c2-46ae-9693-b1f3f931e663'

In [3]:
train, test = competition.get_train_test_split()


In [4]:
test[0]

{'CXSMILES': 'O=C1c2ccc(Cl)cc2[C@@]2(CN1Cc1nnco1)C(=O)N(c1cncc3ccccc13)C[C@@H]2CNc1ncncn1',
 'Chain A Sequence': 'SGLVKMSHPSGDVEACMVQVTCGSMTLNGLWLDNTVWCPRHVMCPADQLSDPNYDALLISMTNHSFSVQKHIGAPANLRVVGHAMQGTLLKLTVDVANPSTPAYTFTTVKPGAAFSVLACYNGRPTGTFTVVMRPNYTIKGSFLCGSCGSVGYTKEGSVINFCYMHQMELANGTHTGSAFDGTMYGAFMDKQVHQVQLTDKYCSVNVVAWLYAAILNGCAWFVKPNRTSVVSFNEWALANQFTEFVGTQSVDMLAVKTGVAIEQLLYAIQQLYTGFQGKQILGSTMLEDEFTPEDVNMQIMGV',
 'Chain B Sequence': 'SGLVKMSHPSGDVEACMVQVTCGSMTLNGLWLDNTVWCPRHVMCPADQLSDPNYDALLISMTNHSFSVQKHIGAPANLRVVGHAMQGTLLKLTVDVANPSTPAYTFTTVKPGAAFSVLACYNGRPTGTFTVVMRPNYTIKGSFLCGSCGSVGYTKEGSVINFCYMHQMELANGTHTGSAFDGTMYGAFMDKQVHQVQLTDKYCSVNVVAWLYAAILNGCAWFVKPNRTSVVSFNEWALANQFTEFVGTQSVDMLAVKTGVAIEQLLYAIQQLYTGFQGKQILGSTMLEDEFTPEDVNMQIMGV',
 'Protein Label': 'MERS-CoV Mpro'}

In [5]:
prot_labels = [t["Protein Label"] for t in test]

In [6]:
test_smiles = [t["CXSMILES"] for t in test]

In [7]:
# write to a file 

In [8]:
with open("test_smiles.txt", "w") as f:
    for s in test_smiles:
        f.write(f"{s}\n")

In [9]:
from asapdiscovery.data.readers.molfile import MolFileFactory


query_ligands = MolFileFactory(filename="test_smiles.txt").load()


In [10]:
query_ligands[0].smiles

'c1ccc2c(c1)cncc2N3C[C@@H]([C@@]4(C3=O)CN(C(=O)c5c4cc(cc5)Cl)Cc6nnco6)CNc7ncncn7'

In [11]:
len(test_smiles)

195

In [12]:
len(query_ligands)

195

In [13]:
for ql, ts in zip(query_ligands, test_smiles):
    ql.tags = {"polaris_smiles": ts}

In [14]:
query_ligands[0].tags

{'polaris_smiles': 'O=C1c2ccc(Cl)cc2[C@@]2(CN1Cc1nnco1)C(=O)N(c1cncc3ccccc13)C[C@@H]2CNc1ncncn1'}

In [15]:
from asapdiscovery.data.util.dask_utils import BackendType, make_dask_client_meta, DaskType
from asapdiscovery.docking.scorer import ChemGauss4Scorer


dask_client = make_dask_client_meta(DaskType.LOCAL)

2025-02-04 13:45:58,986 - distributed.http.proxy - INFO - To route to workers diagnostics web server please install jupyter-server-proxy: python -m pip install jupyter-server-proxy
2025-02-04 13:45:59,010 - distributed.scheduler - INFO - State start
2025-02-04 13:45:59,035 - distributed.scheduler - INFO -   Scheduler at:     tcp://127.0.0.1:39553
2025-02-04 13:45:59,036 - distributed.scheduler - INFO -   dashboard at:  http://127.0.0.1:8787/status
2025-02-04 13:45:59,036 - distributed.scheduler - INFO - Registering Worker plugin shuffle
2025-02-04 13:45:59,072 - distributed.nanny - INFO -         Start Nanny at: 'tcp://127.0.0.1:38875'
2025-02-04 13:45:59,074 - distributed.nanny - INFO -         Start Nanny at: 'tcp://127.0.0.1:36393'
2025-02-04 13:45:59,075 - distributed.nanny - INFO -         Start Nanny at: 'tcp://127.0.0.1:37823'
2025-02-04 13:45:59,076 - distributed.nanny - INFO -         Start Nanny at: 'tcp://127.0.0.1:43179'
2025-02-04 13:45:59,078 - distributed.nanny - INFO - 

In [16]:
dask_client

<Client: 'tcp://127.0.0.1:39553' processes=16 threads=16, memory=124.95 GiB>

In [17]:
from asapdiscovery.modeling.protein_prep import ProteinPrepper
from asapdiscovery.data.schema.complex import Complex
from asapdiscovery.data.readers.structure_dir import StructureDirFactory 

In [18]:
factory = StructureDirFactory(parent_dir="./TRAIN_COMPLEX_PDBS_ONLY_A/")
complexes = factory.load(use_dask=True, dask_client=dask_client)

In [19]:
sars_align_path = "./ligand-posing/ALIGNMENT_REFERENCES/SARS-CoV-2-Mpro/reference_structure/complex.pdb"

In [20]:
mers_align_path = "./ligand-posing/ALIGNMENT_REFERENCES/MERS-CoV-Mpro/reference_structure/complex.pdb"

In [21]:
structure_cache_dir = "./structure_cache"

In [22]:
        ref_complex_SARS = Complex.from_pdb(
            sars_align_path,
            target_kwargs={"target_name": "ref_sars"},
            ligand_kwargs={"compound_name": "ref_ligand_sars"},
        )

In [23]:
ref_complex_MERS = Complex.from_pdb(
            mers_align_path,
            target_kwargs={"target_name": "ref_sars"},
            ligand_kwargs={"compound_name": "ref_ligand_sars"},
        )

In [24]:
    prepper = ProteinPrepper(
        cache_dir=structure_cache_dir,
        align=ref_complex_SARS,
        ref_chain="A",
        active_site_chain="A"
    )

    prepped_complexes = prepper.prep(
        complexes,
        use_dask=True,
        dask_client=dask_client,
        failure_mode="skip",
        cache_dir=structure_cache_dir,
    )
    del complexes



/home/hmacdope/mambaforge/envs/asap_v13/lib/python3.11/site-packages/distributed/client.py:3149: UserWarning: Sending large graph of size 254.88 MiB.
This may cause some slowdown.
Consider scattering data ahead of time and using futures.
  warnings.warn(
No BioAssembly transforms found, using input molecule as biounit: _chainA_UNK
Iridium - Structure: _chainA_UNK has no REMARK data
No BioAssembly transforms found, using input molecule as biounit: _chainA_UNK
Iridium - Structure: _chainA_UNK has no REMARK data
No BioAssembly transforms found, using input molecule as biounit: _chainA_UNK
No BioAssembly transforms found, using input molecule as biounit: _chainA_UNK
Iridium - Structure: _chainA_UNK has no REMARK data
Iridium - Structure: _chainA_UNK has no REMARK data
No BioAssembly transforms found, using input molecule as biounit: _chainA_UNK
Iridium - Structure: _chainA_UNK has no REMARK data
No BioAssembly transforms found, using input molecule as biounit: _chainA_UNK
Iridium - Structu

In [25]:
prepper.cache(prepped_complexes, structure_cache_dir)


In [26]:

import datamol as dm
import numpy as np

from tqdm import tqdm

# y_pred = []

# for x in tqdm(test): 

#     # Generate a random conformer
#     mol = dm.to_mol(x["CXSMILES"])
#     mol = dm.conformers.generate(mol, n_confs=1)

#     # That's our prediction
#     y_pred.append(mol)

In [27]:
from asapdiscovery.data.operators.selectors.mcs_selector import RascalMCESSelector

selector = RascalMCESSelector()
pairs = selector.select(
        query_ligands,
        prepped_complexes,
        n_select=5,
        use_dask=True,
        dask_client=dask_client,
        failure_mode="skip"
    )

[14:03:31] Explicit valence for atom # 15 C, 5, is greater than permitted
[14:03:31] Explicit valence for atom # 19 C, 5, is greater than permitted
[14:03:31] Explicit valence for atom # 15 C, 5, is greater than permitted
[14:03:31] Explicit valence for atom # 15 C, 5, is greater than permitted
[14:03:31] Explicit valence for atom # 19 C, 5, is greater than permitted
[14:03:31] Explicit valence for atom # 15 C, 5, is greater than permitted
[14:03:32] Explicit valence for atom # 19 C, 5, is greater than permitted
[14:03:32] Explicit valence for atom # 15 C, 5, is greater than permitted
[14:03:32] Explicit valence for atom # 15 C, 5, is greater than permitted
[14:03:32] Explicit valence for atom # 15 C, 5, is greater than permitted
[14:03:32] Explicit valence for atom # 19 C, 5, is greater than permitted
[14:03:32] Explicit valence for atom # 15 C, 5, is greater than permitted
[14:03:32] Explicit valence for atom # 15 C, 5, is greater than permitted
[14:03:33] Explicit valence for atom #

In [28]:
from asapdiscovery.docking.openeye import POSITDocker

docker = POSITDocker(
        use_omega=False,
        allow_retries=True,
        last_ditch_fred=True,
    )
results = docker.dock(
        pairs,
        output_dir="docking_results",
        use_dask=True,
        dask_client=dask_client,
        failure_mode="skip",
        return_for_disk_backend=False,
    )


/home/hmacdope/mambaforge/envs/asap_v13/lib/python3.11/site-packages/distributed/client.py:3149: UserWarning: Sending large graph of size 124.53 MiB.
This may cause some slowdown.
Consider scattering data ahead of time and using futures.
  warnings.warn(
2025-02-04 14:05:10,167 - distributed.core - INFO - Event loop was unresponsive in Worker for 4.05s.  This is often caused by long-running GIL-holding functions or moving large chunks of data. This can cause timeouts and instability.
2025-02-04 14:05:13,157 - distributed.core - INFO - Event loop was unresponsive in Worker for 7.04s.  This is often caused by long-running GIL-holding functions or moving large chunks of data. This can cause timeouts and instability.
2025-02-04 14:05:16,798 - distributed.core - INFO - Event loop was unresponsive in Worker for 10.74s.  This is often caused by long-running GIL-holding functions or moving large chunks of data. This can cause timeouts and instability.
2025-02-04 14:05:18,809 - distributed.core

In [29]:
from asapdiscovery.docking.scorer import (
    ChemGauss4Scorer,
    MetaScorer,
)

scorers = [ChemGauss4Scorer()]
scorer = MetaScorer(scorers=scorers)



scores_df = scorer.score(
        results,
        use_dask=True,
        dask_client=dask_client,
        failure_mode="skip",
        return_df=True,
        backend="in-memory",
)



/home/hmacdope/mambaforge/envs/asap_v13/lib/python3.11/site-packages/distributed/client.py:3149: UserWarning: Sending large graph of size 1.09 GiB.
This may cause some slowdown.
Consider scattering data ahead of time and using futures.
  warnings.warn(
2025-02-04 14:36:10,366 - distributed.core - INFO - Event loop was unresponsive in Worker for 5.46s.  This is often caused by long-running GIL-holding functions or moving large chunks of data. This can cause timeouts and instability.
2025-02-04 14:36:11,032 - distributed.core - INFO - Event loop was unresponsive in Worker for 6.11s.  This is often caused by long-running GIL-holding functions or moving large chunks of data. This can cause timeouts and instability.
2025-02-04 14:36:11,045 - distributed.core - INFO - Event loop was unresponsive in Worker for 6.14s.  This is often caused by long-running GIL-holding functions or moving large chunks of data. This can cause timeouts and instability.
2025-02-04 14:36:11,056 - distributed.core - 

In [30]:
scores_df.to_csv("docking_scores_raw.csv", index=False)

In [31]:
scores_df

score_type  pose_id                docking-structure-POSIT  \
0                 0  SARS-CoV-2_Mpro-J0105_0A_CONFIDENTIAL   
1                 0  SARS-CoV-2_Mpro-P0016_0A_CONFIDENTIAL   
2                 0  SARS-CoV-2_Mpro-P0016_0A_CONFIDENTIAL   
3                 0  SARS-CoV-2_Mpro-P0016_0A_CONFIDENTIAL   
4                 0  SARS-CoV-2_Mpro-P0016_0A_CONFIDENTIAL   
..              ...                                    ...   
970               0  SARS-CoV-2_Mpro-x3366_0A_CONFIDENTIAL   
971               0  SARS-CoV-2_Mpro-z7b2u_0A_CONFIDENTIAL   
972               0  SARS-CoV-2_Mpro-z7b2u_0B_CONFIDENTIAL   
973               0  SARS-CoV-2_Mpro-z7tll_0A_CONFIDENTIAL   
974               0  SARS-CoV-2_Mpro-z7tll_0B_CONFIDENTIAL   

score_type                              complex_ligand_smiles  \
0           C[C@H](c1cccc(c1)C(F)(F)F)N(C2CC2)C(=O)CN3c4cc...   
1                 c1ccc2c(c1)cncc2CC(=O)N(CCC3CCCCC3)Cc4cccs4   
2                 c1ccc2c(c1)cncc2CC(=O)N(CCC3CCCCC3)Cc4cccs4   
3                 c1ccc2c(c1)cncc2CC(=O)N(CCC3CCCCC3)Cc4cccs4   
4                 c1ccc2c(c1)cncc2CC(=O)N(CCC3CCCCC3)Cc4cccs4   
..                                                        ...   
970                        Cc1ccncc1NC(=O)Cc2ccc3c(c2)nc[nH]3   
971                  c1c(cncc1F)n2c(c([nH]c2=O)CC3CCCCC3)[O-]   
972                  c1c(cncc1F)n2c(c([nH]c2=O)CC3CCCCC3)[O-]   
973         CC1([C@@H]2[C@H]1[C@H](N(C2)C(=O)[C@H](C(C)(C)...   
974         CC1([C@@H]2[C@H]1[C@H](N(C2)C(=O)[C@H](C(C)(C)...   

score_type  docking-confidence-POSIT target_identifiers           ligand_id  \
0                               0.33                NaN   unknown_ligand_56   
1                               0.14                NaN   unknown_ligand_18   
2                               0.18                NaN  unknown_ligand_171   
3                               0.18                NaN  unknown_ligand_180   
4                               0.18                NaN   unknown_ligand_63   
..                               ...                ...                 ...   
970                             0.24                NaN   unknown_ligand_78   
971                             0.78                NaN   unknown_ligand_31   
972                             0.78                NaN   unknown_ligand_31   
973                             0.91                NaN  unknown_ligand_154   
974                             0.91                NaN  unknown_ligand_154   

score_type                                             SMILES  \
0            CC[C@H]1C[C@H](CCN1C(=O)Cc2cncc3c2cccc3)C(F)(F)F   
1                      C[C@@H]1CCN(CC=C1)C(=O)Cc2cncc3c2cccc3   
2           C[C@H]1CCN([C@H](C1)c2ccccc2OC)C(=O)Cc3cncc4c3...   
3                          CC1(CCN(CC1)C(=O)Cc2cncc3c2cccc3)C   
4               c1ccc2c(c1)cncc2CC(=O)N3CCC[C@@H]3c4cccc(c4)F   
..                                                        ...   
970         CC(=O)N1C[C@@H]2C[C@H]1c3n2c(=O)n(c3[O-])c4cnc...   
971             C[C@@H]1CCc2c(n(c(=O)n2C1)c3cncc4c3cccc4)[O-]   
972             C[C@@H]1CCc2c(n(c(=O)n2C1)c3cncc4c3cccc4)[O-]   
973         CC(C)(C)[C@@H](C(=O)N1C[C@@H](C[C@H]1C(=O)N[C@...   
974         CC(C)(C)[C@@H](C(=O)N1C[C@@H](C[C@H]1C(=O)N[C@...   

score_type                     INCHIKEY ligand_identifiers  \
0           GRKRTLABFVOMTK-HOTGVXAUSA-N                NaN   
1           KAVXTDDRPHSLHV-AWEZNQCLSA-N                NaN   
2           QGRHAQONDNPCDI-HTAPYJJXSA-N                NaN   
3           IAUMFAKYYCHQHH-UHFFFAOYSA-N                NaN   
4           ZUTBTFXLTPFNNC-HXUWFJFHSA-N                NaN   
..                                  ...                ...   
970         FLHZMOBXQOJTSF-JSGCOSHPSA-M                NaN   
971         FXNXRHJJLOXDEH-LLVKDONJSA-M                NaN   
972         FXNXRHJJLOXDEH-LLVKDONJSA-M                NaN   
973         UJGYRQGIZAPYNF-AIEDFZFUSA-O                NaN   
974         UJGYRQGIZAPYNF-AIEDFZFUSA-O                NaN   


In [32]:
scores_df["ligand_id"].nunique()

195

In [33]:
    scores_df = scores_df.sort_values(
        "docking-score-POSIT", ascending=True
    )

In [34]:
scores_df

score_type  pose_id                 docking-structure-POSIT  \
917               0  SARS-CoV-2_Mpro-x12177_0A_CONFIDENTIAL   
84                0   SARS-CoV-2_Mpro-P0057_0A_CONFIDENTIAL   
105               0   SARS-CoV-2_Mpro-P0057_0B_CONFIDENTIAL   
887               0  SARS-CoV-2_Mpro-x11354_0A_CONFIDENTIAL   
95                0   SARS-CoV-2_Mpro-P0057_0B_CONFIDENTIAL   
..              ...                                     ...   
920               0  SARS-CoV-2_Mpro-x12350_0A_CONFIDENTIAL   
843               0   SARS-CoV-2_Mpro-x0426_0A_CONFIDENTIAL   
289               0   SARS-CoV-2_Mpro-P2242_0A_CONFIDENTIAL   
102               0   SARS-CoV-2_Mpro-P0057_0B_CONFIDENTIAL   
211               0   SARS-CoV-2_Mpro-P2178_0A_CONFIDENTIAL   

score_type                              complex_ligand_smiles  \
917           COc1ccc(cc1)N(Cc2cccc(c2)Cl)C(=O)CN3c4ccccc4NN3   
84          C[NH+](C)C1C=CC(N=C1)N(Cc2cccc(c2)Cl)C(=O)Cc3c...   
105         C[NH+](C)C1C=CC(N=C1)N(Cc2cccc(c2)Cl)C(=O)Cc3c...   
887                       Cc1ccncc1CC(=O)Nc2cccc3c2C[NH2+]CC3   
95          C[NH+](C)C1C=CC(N=C1)N(Cc2cccc(c2)Cl)C(=O)Cc3c...   
..                                                        ...   
920           CC(C)OCCCN(Cc1ccco1)C(=O)Nc2cn(c(=O)c3c2cccc3)C   
843                             c1ccc(c(c1)C(=O)NCCc2ccncc2)F   
289         CCCNC(=O)CN1C[C@H](c2cc(ccc2C1=O)Cl)C(=O)Nc3cn...   
102         C[NH+](C)C1C=CC(N=C1)N(Cc2cccc(c2)Cl)C(=O)Cc3c...   
211         Cc1cccc2c1c(cnc2)NC(=O)[C@@H]3C[N@H+](Cc4c3cc(...   

score_type  docking-confidence-POSIT target_identifiers           ligand_id  \
917                             0.83                NaN    unknown_ligand_1   
84                              0.79                NaN  unknown_ligand_152   
105                             0.79                NaN  unknown_ligand_152   
887                             0.33                NaN  unknown_ligand_120   
95                              0.42                NaN   unknown_ligand_97   
..                               ...                ...                 ...   
920                             0.14                NaN   unknown_ligand_95   
843                             0.78                NaN  unknown_ligand_192   
289                             0.87                NaN   unknown_ligand_40   
102                             0.72                NaN  unknown_ligand_140   
211                             0.69                NaN   unknown_ligand_50   

score_type                                             SMILES  \
917          COc1ccc(cc1)N(Cc2cccc(c2)Cl)C(=O)Cc3cncc4c3cccc4   
84          CC(C)(C#N)c1ccc(cc1)N(Cc2cccc(c2)Cl)C(=O)Cc3cn...   
105         CC(C)(C#N)c1ccc(cc1)N(Cc2cccc(c2)Cl)C(=O)Cc3cn...   
887                     c1ccc2c(c1)cncc2CC(=O)N3CCC4(CCC4)CC3   
95          CCC(=O)Nc1cccc(c1)N(Cc2ccccc2)C(=O)Cc3cncc4c3c...   
..                                                        ...   
920         CCNC(=O)C(=C)CN(c1cccc(c1)Cl)C(=O)Nc2cncc3c2cccc3   
843                      c1ccc2c(c1)cncc2CC(=O)NCc3cccc(c3)Cl   
289         c1ccc2c(c1)cncc2NC(=O)[C@@H]3C[N@H+](Cc4c3cc(c...   
102         CCC(=O)N1CCCc2c1cc(cc2)N(Cc3cccc(c3)Cl)C(=O)Cc...   
211         c1ccc2c(c1)cncc2NC(=O)[C@@H]3C[N@H+](Cc4c3cc(c...   

score_type                     INCHIKEY ligand_identifiers  \
917         LRGKWKMIZJJVJM-UHFFFAOYSA-N                NaN   
84          HOSYWXDLYYCTEQ-UHFFFAOYSA-N                NaN   
105         HOSYWXDLYYCTEQ-UHFFFAOYSA-N                NaN   
887         ZEPNBRUOHBYYPR-UHFFFAOYSA-N                NaN   
95          GULWMYIDTZEZPJ-UHFFFAOYSA-N                NaN   
..                                  ...                ...   
920         KSVPMMUUJFSGJU-UHFFFAOYSA-N                NaN   
843         PHUYFUIXFJFGGJ-UHFFFAOYSA-N                NaN   
289         OFURFNPRYDIXAI-AREMUKBSSA-O                NaN   
102         JVQONISACHJVKP-UHFFFAOYSA-N                NaN   
211         IGFMQVXQADZXOR-HHHXNRCGSA-O           

In [35]:
    # remove duplicates that are the same compound docked to different structures
    unique = scores_df.drop_duplicates(
        subset=["ligand_id"], keep="first"
    )

In [36]:
unique

score_type  pose_id                 docking-structure-POSIT  \
917               0  SARS-CoV-2_Mpro-x12177_0A_CONFIDENTIAL   
84                0   SARS-CoV-2_Mpro-P0057_0A_CONFIDENTIAL   
887               0  SARS-CoV-2_Mpro-x11354_0A_CONFIDENTIAL   
95                0   SARS-CoV-2_Mpro-P0057_0B_CONFIDENTIAL   
888               0  SARS-CoV-2_Mpro-x11354_0A_CONFIDENTIAL   
..              ...                                     ...   
972               0   SARS-CoV-2_Mpro-z7b2u_0B_CONFIDENTIAL   
191               0   SARS-CoV-2_Mpro-P1090_0A_CONFIDENTIAL   
6                 0   SARS-CoV-2_Mpro-P0016_0A_CONFIDENTIAL   
196               0   SARS-CoV-2_Mpro-P1835_0A_CONFIDENTIAL   
61                0   SARS-CoV-2_Mpro-P0022_0B_CONFIDENTIAL   

score_type                              complex_ligand_smiles  \
917           COc1ccc(cc1)N(Cc2cccc(c2)Cl)C(=O)CN3c4ccccc4NN3   
84          C[NH+](C)C1C=CC(N=C1)N(Cc2cccc(c2)Cl)C(=O)Cc3c...   
887                       Cc1ccncc1CC(=O)Nc2cccc3c2C[NH2+]CC3   
95          C[NH+](C)C1C=CC(N=C1)N(Cc2cccc(c2)Cl)C(=O)Cc3c...   
888                       Cc1ccncc1CC(=O)Nc2cccc3c2C[NH2+]CC3   
..                                                        ...   
972                  c1c(cncc1F)n2c(c([nH]c2=O)CC3CCCCC3)[O-]   
191         CNC(=O)C[N@H+]1Cc2ccc(cc2[C@@H](C1)C(=O)Nc3cnc...   
6                 c1ccc2c(c1)cncc2CC(=O)N(CCC3CCCCC3)Cc4cccs4   
196         CNC(=O)CN1C[C@H](c2cc(ccc2C1=O)Cl)C(=O)Nc3cncc...   
61          c1ccc2c(c1)cncc2N3C(=O)[C@@]4(CCOc5c4cc(cc5)Cl...   

score_type  docking-confidence-POSIT target_identifiers           ligand_id  \
917                             0.83                NaN    unknown_ligand_1   
84                              0.79                NaN  unknown_ligand_152   
887                             0.33                NaN  unknown_ligand_120   
95                              0.42                NaN   unknown_ligand_97   
888                             0.33                NaN  unknown_ligand_121   
..                               ...                ...                 ...   
972                             0.78                NaN   unknown_ligand_31   
191                             0.89                NaN   unknown_ligand_40   
6                               0.33                NaN   unknown_ligand_89   
196                             0.69                NaN   unknown_ligand_50   
61                              0.72                NaN  unknown_ligand_172   

score_type                                             SMILES  \
917          COc1ccc(cc1)N(Cc2cccc(c2)Cl)C(=O)Cc3cncc4c3cccc4   
84          CC(C)(C#N)c1ccc(cc1)N(Cc2cccc(c2)Cl)C(=O)Cc3cn...   
887                     c1ccc2c(c1)cncc2CC(=O)N3CCC4(CCC4)CC3   
95          CCC(=O)Nc1cccc(c1)N(Cc2ccccc2)C(=O)Cc3cncc4c3c...   
888                     c1ccc2c(c1)cncc2CC(=O)N3CCC(CC3)C4CC4   
..                                                        ...   
972             C[C@@H]1CCc2c(n(c(=O)n2C1)c3cncc4c3cccc4)[O-]   
191         c1ccc2c(c1)cncc2NC(=O)[C@@H]3C[N@H+](Cc4c3cc(c...   
6           c1ccc2c(c1)cncc2CC(=O)N(Cc3cccc(c3)Cl)C45CC(C4...   
196         c1ccc2c(c1)cncc2NC(=O)[C@@H]3C[N@H+](Cc4c3cc(c...   
61          c1ccc2c(c1)cncc2N3C(=O)[C@]4(CCOc5c4cc(cc5)S(=...   

score_type                     INCHIKEY ligand_identifiers  \
917         LRGKWKMIZJJVJM-UHFFFAOYSA-N                NaN   
84          HOSYWXDLYYCTEQ-UHFFFAOYSA-N                NaN   
887         ZEPNBRUOHBYYPR-UHFFFAOYSA-N                NaN   
95          GULWMYIDTZEZPJ-UHFFFAOYSA-N                NaN   
888         XGAXVWRMZLCNLB-UHFFFAOYSA-N                NaN   
..                                  ...                ...   
972         FXNXRHJJLOXDEH-LLVKDONJSA-M                NaN   
191         OFURFNPRYDIXAI-AREMUKBSSA-O                NaN   
6           GYUYAEQBOLBVTL-OJBMAJLDSA-O                NaN   
196         IGFMQVXQADZXOR-HHHXNRCGSA-O                NaN   
61          JGUHJQWOUHEHHJ-HXUWFJFHSA-N           

In [37]:
test_inchis = [dm.to_inchikey(t) for t in test_smiles]

In [38]:
protein_labels = [t["Protein Label"] for t in test ] # need to jam into df

2025-02-04 14:37:19,381 - distributed.utils_perf - WARNING - full garbage collections took 24% CPU time recently (threshold: 10%)


In [39]:
unique["lig_id_no"] = unique["ligand_id"].apply(lambda x: int(x.split("_")[-1]))

/tmp/ipykernel_58255/1748029362.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  unique["lig_id_no"] = unique["ligand_id"].apply(lambda x: int(x.split("_")[-1]))


In [40]:
unique.sort_values("lig_id_no")

score_type  pose_id                 docking-structure-POSIT  \
461               0   SARS-CoV-2_Mpro-P2487_0B_CONFIDENTIAL   
917               0  SARS-CoV-2_Mpro-x12177_0A_CONFIDENTIAL   
356               0   SARS-CoV-2_Mpro-P2487_0A_CONFIDENTIAL   
426               0   SARS-CoV-2_Mpro-P2487_0A_CONFIDENTIAL   
460               0   SARS-CoV-2_Mpro-P2487_0B_CONFIDENTIAL   
..              ...                                     ...   
209               0   SARS-CoV-2_Mpro-P2099_0B_CONFIDENTIAL   
355               0   SARS-CoV-2_Mpro-P2487_0A_CONFIDENTIAL   
69                0   SARS-CoV-2_Mpro-P0057_0A_CONFIDENTIAL   
372               0   SARS-CoV-2_Mpro-P2487_0A_CONFIDENTIAL   
948               0  SARS-CoV-2_Mpro-x12686_0A_CONFIDENTIAL   

score_type                              complex_ligand_smiles  \
461         CNC(=O)CN1C[C@]2(CCN(C2=O)c3cncc4c3cccc4)c5cc(...   
917           COc1ccc(cc1)N(Cc2cccc(c2)Cl)C(=O)CN3c4ccccc4NN3   
356         CNC(=O)CN1C[C@]2(CCN(C2=O)c3cncc4c3cccc4)c5cc(...   
426         CNC(=O)CN1C[C@]2(CCN(C2=O)c3cncc4c3cccc4)c5cc(...   
460         CNC(=O)CN1C[C@]2(CCN(C2=O)c3cncc4c3cccc4)c5cc(...   
..                                                        ...   
209         c1ccc2c(c1)cncc2NC(=O)[C@@H]3CNS(=O)(=O)c4c3cc...   
355         CNC(=O)CN1C[C@]2(CCN(C2=O)c3cncc4c3cccc4)c5cc(...   
69          C[NH+](C)C1C=CC(N=C1)N(Cc2cccc(c2)Cl)C(=O)Cc3c...   
372         CNC(=O)CN1C[C@]2(CCN(C2=O)c3cncc4c3cccc4)c5cc(...   
948         c1ccc2c(c1)cncc2N3C(=O)[C@@]4(CCOc5c4cc(cc5)Cl...   

score_type  docking-confidence-POSIT target_identifiers           ligand_id  \
461                             0.78                NaN    unknown_ligand_0   
917                             0.83                NaN    unknown_ligand_1   
356                             0.82                NaN    unknown_ligand_2   
426                             0.91                NaN    unknown_ligand_3   
460                             0.69                NaN    unknown_ligand_4   
..                               ...                ...                 ...   
209                             0.24                NaN  unknown_ligand_190   
355                             0.82                NaN  unknown_ligand_191   
69                              0.18                NaN  unknown_ligand_192   
372                             0.85                NaN  unknown_ligand_193   
948                             0.91                NaN  unknown_ligand_194   

score_type                                             SMILES  \
461         c1ccc2c(c1)cncc2N3C[C@@H]([C@@]4(C3=O)CN(C(=O)...   
917          COc1ccc(cc1)N(Cc2cccc(c2)Cl)C(=O)Cc3cncc4c3cccc4   
356         CNC(=O)CN1C[C@@]2(c3cc(ccc3C1=O)Cl)[C@H](CN(C2...   
426         CNC(=O)CN1C[C@@]2(c3cc(ccc3C1=O)Cl)[C@H](CN(C2...   
460         c1ccc2c(c1)cncc2N3C[C@@H]([C@@]4(C3=O)CN(C(=O)...   
..                                                        ...   
209         C[C@@H](c1cc(cc(c1)Cl)c2ccc(cc2)S(=O)(=O)N)NC(...   
355         CNC(=O)CN1C[C@@]2(c3cc(ccc3C1=O)Cl)[C@H](CN(C2...   
69                       c1ccc2c(c1)cncc2CC(=O)NCc3cccc(c3)Cl   
372         CC(C)OC[C@H]1CN(C(=O)[C@@]12CN(C(=O)c3c2cc(cc3...   
948         C[C@H]1C[C@@]2(COC1)C(=O)N(C(=O)N2)c3cncc4c3cccc4   

score_type                     INCHIKEY ligand_identifiers  \
461         INRDDGOELGFOMA-JMQGSBJISA-N                NaN   
917         LRGKWKMIZJJVJM-UHFFFAOYSA-N                NaN   
356         KZXBBCDPQDLZRG-SLQAJWMNSA-N                NaN   
426         KQNOKAYCKGIXFU-GBXCKJPGSA-O                NaN   
460         NRGQSDUOQHOVFB-UGDMGKLASA-N                NaN   
..                                  ...                ...   
209         CDIRCRIIKZGBTI-NSHDSACASA-N                NaN   
355         KZXBBCDPQDLZRG-SLQAJWMNSA-N                NaN   
69          PHUYFUIXFJFGGJ-UHFFFAOYSA-N                NaN   
372         OEHDDAARDCUYDF-GDJIYFAZSA-N                NaN   
948         XDTMINXNKFSUDN-APPDUMDISA-N           

In [41]:
unique.set_index("lig_id_no").loc[154]

score_type
pose_id                                                                     0
docking-structure-POSIT                 SARS-CoV-2_Mpro-z7tll_0A_CONFIDENTIAL
complex_ligand_smiles       CC1([C@@H]2[C@H]1[C@H](N(C2)C(=O)[C@H](C(C)(C)...
docking-confidence-POSIT                                                 0.91
target_identifiers                                                        NaN
ligand_id                                                  unknown_ligand_154
SMILES                      CC(C)(C)[C@@H](C(=O)N1C[C@@H](C[C@H]1C(=O)N[C@...
INCHIKEY                                          UJGYRQGIZAPYNF-AIEDFZFUSA-O
ligand_identifiers                                                        NaN
input                       type='POSITDockingResults' input_pair=DockingI...
docking-score-POSIT                                                 -8.621801
Name: 154, dtype: object

In [42]:
!mkdir -p best_poses

In [47]:
def make_pose(id_no, inp):
    path = f"./best_poses/{id_no}.pdb"
    inp.to_posed_complex().to_pdb(path)
    return path

In [48]:
unique['protein_path'] = unique.apply(lambda x: make_pose(x.lig_id_no, x.input), axis=1)

2025-02-04 14:40:24,204 - distributed.utils_perf - WARNING - full garbage collections took 24% CPU time recently (threshold: 10%)
2025-02-04 14:40:27,853 - distributed.utils_perf - WARNING - full garbage collections took 24% CPU time recently (threshold: 10%)
2025-02-04 14:40:31,648 - distributed.utils_perf - WARNING - full garbage collections took 24% CPU time recently (threshold: 10%)
2025-02-04 14:40:35,543 - distributed.utils_perf - WARNING - full garbage collections took 24% CPU time recently (threshold: 10%)
/tmp/ipykernel_58255/3119141169.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  unique['protein_path'] = unique.apply(lambda x: make_pose(x.lig_id_no, x.input), axis=1)


In [ ]:
# # Load the reference and mobile structure
# def align(ref_path):
# ref_path = path / "SARS-CoV-2-Mpro" / "complex.pdb"
# pymol.cmd.load(, "mobile")
# pymol.cmd.load(ref_path, "reference")
# pymol.cmd.align(
#     "polymer and name CA and mobile",
#     "polymer and name CA and reference",
#     quiet=0,
# );

In [ ]:
# def serialize_rdkit_mol(mol: Chem.Mol): 
#     props = Chem.PropertyPickleOptions.AllProps
#     mol_bytes = mol.ToBinary(props)
#     return base64.b64encode(mol_bytes).decode('ascii')  

# y_pred_serialized = [serialize_rdkit_mol(mol) for mol in y_pred]

In [ ]:

# deserialized = Chem.Mol(base64.b64decode(y_pred_serialized[0].encode("ascii")))
# deserialized

In [49]:
unique

score_type  pose_id                 docking-structure-POSIT  \
917               0  SARS-CoV-2_Mpro-x12177_0A_CONFIDENTIAL   
84                0   SARS-CoV-2_Mpro-P0057_0A_CONFIDENTIAL   
887               0  SARS-CoV-2_Mpro-x11354_0A_CONFIDENTIAL   
95                0   SARS-CoV-2_Mpro-P0057_0B_CONFIDENTIAL   
888               0  SARS-CoV-2_Mpro-x11354_0A_CONFIDENTIAL   
..              ...                                     ...   
972               0   SARS-CoV-2_Mpro-z7b2u_0B_CONFIDENTIAL   
191               0   SARS-CoV-2_Mpro-P1090_0A_CONFIDENTIAL   
6                 0   SARS-CoV-2_Mpro-P0016_0A_CONFIDENTIAL   
196               0   SARS-CoV-2_Mpro-P1835_0A_CONFIDENTIAL   
61                0   SARS-CoV-2_Mpro-P0022_0B_CONFIDENTIAL   

score_type                              complex_ligand_smiles  \
917           COc1ccc(cc1)N(Cc2cccc(c2)Cl)C(=O)CN3c4ccccc4NN3   
84          C[NH+](C)C1C=CC(N=C1)N(Cc2cccc(c2)Cl)C(=O)Cc3c...   
887                       Cc1ccncc1CC(=O)Nc2cccc3c2C[NH2+]CC3   
95          C[NH+](C)C1C=CC(N=C1)N(Cc2cccc(c2)Cl)C(=O)Cc3c...   
888                       Cc1ccncc1CC(=O)Nc2cccc3c2C[NH2+]CC3   
..                                                        ...   
972                  c1c(cncc1F)n2c(c([nH]c2=O)CC3CCCCC3)[O-]   
191         CNC(=O)C[N@H+]1Cc2ccc(cc2[C@@H](C1)C(=O)Nc3cnc...   
6                 c1ccc2c(c1)cncc2CC(=O)N(CCC3CCCCC3)Cc4cccs4   
196         CNC(=O)CN1C[C@H](c2cc(ccc2C1=O)Cl)C(=O)Nc3cncc...   
61          c1ccc2c(c1)cncc2N3C(=O)[C@@]4(CCOc5c4cc(cc5)Cl...   

score_type  docking-confidence-POSIT target_identifiers           ligand_id  \
917                             0.83                NaN    unknown_ligand_1   
84                              0.79                NaN  unknown_ligand_152   
887                             0.33                NaN  unknown_ligand_120   
95                              0.42                NaN   unknown_ligand_97   
888                             0.33                NaN  unknown_ligand_121   
..                               ...                ...                 ...   
972                             0.78                NaN   unknown_ligand_31   
191                             0.89                NaN   unknown_ligand_40   
6                               0.33                NaN   unknown_ligand_89   
196                             0.69                NaN   unknown_ligand_50   
61                              0.72                NaN  unknown_ligand_172   

score_type                                             SMILES  \
917          COc1ccc(cc1)N(Cc2cccc(c2)Cl)C(=O)Cc3cncc4c3cccc4   
84          CC(C)(C#N)c1ccc(cc1)N(Cc2cccc(c2)Cl)C(=O)Cc3cn...   
887                     c1ccc2c(c1)cncc2CC(=O)N3CCC4(CCC4)CC3   
95          CCC(=O)Nc1cccc(c1)N(Cc2ccccc2)C(=O)Cc3cncc4c3c...   
888                     c1ccc2c(c1)cncc2CC(=O)N3CCC(CC3)C4CC4   
..                                                        ...   
972             C[C@@H]1CCc2c(n(c(=O)n2C1)c3cncc4c3cccc4)[O-]   
191         c1ccc2c(c1)cncc2NC(=O)[C@@H]3C[N@H+](Cc4c3cc(c...   
6           c1ccc2c(c1)cncc2CC(=O)N(Cc3cccc(c3)Cl)C45CC(C4...   
196         c1ccc2c(c1)cncc2NC(=O)[C@@H]3C[N@H+](Cc4c3cc(c...   
61          c1ccc2c(c1)cncc2N3C(=O)[C@]4(CCOc5c4cc(cc5)S(=...   

score_type                     INCHIKEY ligand_identifiers  \
917         LRGKWKMIZJJVJM-UHFFFAOYSA-N                NaN   
84          HOSYWXDLYYCTEQ-UHFFFAOYSA-N                NaN   
887         ZEPNBRUOHBYYPR-UHFFFAOYSA-N                NaN   
95          GULWMYIDTZEZPJ-UHFFFAOYSA-N                NaN   
888         XGAXVWRMZLCNLB-UHFFFAOYSA-N                NaN   
..                                  ...                ...   
972         FXNXRHJJLOXDEH-LLVKDONJSA-M                NaN   
191         OFURFNPRYDIXAI-AREMUKBSSA-O                NaN   
6           GYUYAEQBOLBVTL-OJBMAJLDSA-O                NaN   
196         IGFMQVXQADZXOR-HHHXNRCGSA-O                NaN   
61          JGUHJQWOUHEHHJ-HXUWFJFHSA-N           

In [53]:
unique.sort_values("lig_id_no", inplace=True)

/tmp/ipykernel_58255/1639678927.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  unique.sort_values("lig_id_no", inplace=True)


In [55]:
unique["protein_label"] = prot_labels

/tmp/ipykernel_58255/3371284925.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  unique["protein_label"] = prot_labels


In [56]:
unique

2025-02-04 14:44:34,752 - distributed.utils_perf - WARNING - full garbage collections took 24% CPU time recently (threshold: 10%)


score_type  pose_id                 docking-structure-POSIT  \
461               0   SARS-CoV-2_Mpro-P2487_0B_CONFIDENTIAL   
917               0  SARS-CoV-2_Mpro-x12177_0A_CONFIDENTIAL   
356               0   SARS-CoV-2_Mpro-P2487_0A_CONFIDENTIAL   
426               0   SARS-CoV-2_Mpro-P2487_0A_CONFIDENTIAL   
460               0   SARS-CoV-2_Mpro-P2487_0B_CONFIDENTIAL   
..              ...                                     ...   
209               0   SARS-CoV-2_Mpro-P2099_0B_CONFIDENTIAL   
355               0   SARS-CoV-2_Mpro-P2487_0A_CONFIDENTIAL   
69                0   SARS-CoV-2_Mpro-P0057_0A_CONFIDENTIAL   
372               0   SARS-CoV-2_Mpro-P2487_0A_CONFIDENTIAL   
948               0  SARS-CoV-2_Mpro-x12686_0A_CONFIDENTIAL   

score_type                              complex_ligand_smiles  \
461         CNC(=O)CN1C[C@]2(CCN(C2=O)c3cncc4c3cccc4)c5cc(...   
917           COc1ccc(cc1)N(Cc2cccc(c2)Cl)C(=O)CN3c4ccccc4NN3   
356         CNC(=O)CN1C[C@]2(CCN(C2=O)c3cncc4c3cccc4)c5cc(...   
426         CNC(=O)CN1C[C@]2(CCN(C2=O)c3cncc4c3cccc4)c5cc(...   
460         CNC(=O)CN1C[C@]2(CCN(C2=O)c3cncc4c3cccc4)c5cc(...   
..                                                        ...   
209         c1ccc2c(c1)cncc2NC(=O)[C@@H]3CNS(=O)(=O)c4c3cc...   
355         CNC(=O)CN1C[C@]2(CCN(C2=O)c3cncc4c3cccc4)c5cc(...   
69          C[NH+](C)C1C=CC(N=C1)N(Cc2cccc(c2)Cl)C(=O)Cc3c...   
372         CNC(=O)CN1C[C@]2(CCN(C2=O)c3cncc4c3cccc4)c5cc(...   
948         c1ccc2c(c1)cncc2N3C(=O)[C@@]4(CCOc5c4cc(cc5)Cl...   

score_type  docking-confidence-POSIT target_identifiers           ligand_id  \
461                             0.78                NaN    unknown_ligand_0   
917                             0.83                NaN    unknown_ligand_1   
356                             0.82                NaN    unknown_ligand_2   
426                             0.91                NaN    unknown_ligand_3   
460                             0.69                NaN    unknown_ligand_4   
..                               ...                ...                 ...   
209                             0.24                NaN  unknown_ligand_190   
355                             0.82                NaN  unknown_ligand_191   
69                              0.18                NaN  unknown_ligand_192   
372                             0.85                NaN  unknown_ligand_193   
948                             0.91                NaN  unknown_ligand_194   

score_type                                             SMILES  \
461         c1ccc2c(c1)cncc2N3C[C@@H]([C@@]4(C3=O)CN(C(=O)...   
917          COc1ccc(cc1)N(Cc2cccc(c2)Cl)C(=O)Cc3cncc4c3cccc4   
356         CNC(=O)CN1C[C@@]2(c3cc(ccc3C1=O)Cl)[C@H](CN(C2...   
426         CNC(=O)CN1C[C@@]2(c3cc(ccc3C1=O)Cl)[C@H](CN(C2...   
460         c1ccc2c(c1)cncc2N3C[C@@H]([C@@]4(C3=O)CN(C(=O)...   
..                                                        ...   
209         C[C@@H](c1cc(cc(c1)Cl)c2ccc(cc2)S(=O)(=O)N)NC(...   
355         CNC(=O)CN1C[C@@]2(c3cc(ccc3C1=O)Cl)[C@H](CN(C2...   
69                       c1ccc2c(c1)cncc2CC(=O)NCc3cccc(c3)Cl   
372         CC(C)OC[C@H]1CN(C(=O)[C@@]12CN(C(=O)c3c2cc(cc3...   
948         C[C@H]1C[C@@]2(COC1)C(=O)N(C(=O)N2)c3cncc4c3cccc4   

score_type                     INCHIKEY ligand_identifiers  \
461         INRDDGOELGFOMA-JMQGSBJISA-N                NaN   
917         LRGKWKMIZJJVJM-UHFFFAOYSA-N                NaN   
356         KZXBBCDPQDLZRG-SLQAJWMNSA-N                NaN   
426         KQNOKAYCKGIXFU-GBXCKJPGSA-O                NaN   
460         NRGQSDUOQHOVFB-UGDMGKLASA-N                NaN   
..                                  ...                ...   
209         CDIRCRIIKZGBTI-NSHDSACASA-N                NaN   
355         KZXBBCDPQDLZRG-SLQAJWMNSA-N                NaN   
69          PHUYFUIXFJFGGJ-UHFFFAOYSA-N                NaN   
372         OEHDDAARDCUYDF-GDJIYFAZSA-N                NaN   
948         XDTMINXNKFSUDN-APPDUMDISA-N           

In [58]:
prot_labels[-1]

'SARS-CoV-2 Mpro'

In [65]:
import pymol

In [1]:
def align_pred(protein_path, ref_type, index, path_prefix):
    pymol.cmd.delete("all")
    if ref_type == 'MERS-CoV Mpro':
        tag = "MERS"
        ref_path = "./ligand-posing/ALIGNMENT_REFERENCES/MERS-CoV-Mpro/reference_structure/complex.pdb"
    elif ref_type == "SARS-CoV-2 Mpro":
        tag = "SARS"
        ref_path = "./ligand-posing/ALIGNMENT_REFERENCES/SARS-CoV-2-Mpro/reference_structure/complex.pdb"
    else:
        raise Exception
    pymol.cmd.load(protein_path, "mobile")
    pymol.cmd.load(ref_path, "reference")
    pymol.cmd.align(
        "chain A and mobile",
        "chain A and reference",
    )
    ret_path = f"{path_prefix}/{index}_{tag}.pdb"
    ret_path_pse = f"{path_prefix}/{index}_{tag}.pse"
    pymol.cmd.save(ret_path_pse)
    pymol.cmd.save(ret_path, "mobile")
    return ret_path
    
    

In [2]:
unique["aligned_path"] = unique.apply(lambda x: align_pred(x.protein_path, x.protein_label, x.lig_id_no, "best_poses_aligned"), axis=1)

NameError: name 'unique' is not defined

In [94]:
unique.set_index("lig_id_no", inplace=True)

In [ ]:
def split_